In [43]:
from bs4 import BeautifulSoup
import requests
import re
import json
import pandas as pd
import os
EXPORT_FOLDER = "../data2/"

In [2]:
# url = "https://www.millenaire3.com/ressources/2023/changer-les-comportements-revue-et-enseignements-des-actions-metropolitaines"
# url2 = "https://www.millenaire3.com/ressources/2023/agir-sur-les-modes-de-vie-une-nouvelle-grille-d-analyse"
# url3 = "https://www.millenaire3.com/dossiers/2022/resilience-quelles-articulations-entre-acteurs-publics-et-initiatives-du-territoire"
# url4 = "https://www.millenaire3.com/dossiers/2022/resilience-quelles-articulations-entre-acteurs-publics-et-initiatives-du-territoire/institut-transitions-notre-but-c-est-de-former-ceux-qui-peuvent-agir-des-aujourd-hui"
# url5 = "https://www.millenaire3.com/dossiers/2022/resilience-quelles-articulations-entre-acteurs-publics-et-initiatives-du-territoire/les-alchimistes-lyon-alimentation-gaspillage-compostage-aucun-de-ces-sujets-ne-laisse-indifferent"
# url6 = "https://www.millenaire3.com/ressources/2023/crise-ecologique-le-metabolisme-de-l-economie-au-caeur-des-enjeux"
# url7 = "https://www.millenaire3.com/dossiers/2015/la-soierie-lyonnaise-entre-tradition-et-innovation-archives/la-soie-a-lyon-une-initiative-du-pouvoir-royal"
# urls = [url, url2, url3, url4, url5, url6, url7]

In [33]:
def get_metadata(soup, type, url, mult_items, errors):

    mult_items[url] = {"auteurs" : [], "tags" : [], "liens" : []}

    #TAGS
    tags_liste = soup.find_all("ul", {"class": "list-inline keywords"})
    tags = []
    for tag in tags_liste:
        a = tag.find_all("a")
        for tag in a:
            if re.search("tag", tag["href"]) != None:
                tags += tag.contents
    if len(tags) > 0:
        mult_items[url]["tags"] = tags
    else:
        mult_items[url]["tags"] = "NA"

    #AUTHORS
    if type == "Interview":
        liste = soup.find_all("ul", {"class": "list-inline keywords"})
        authors = []
        for elem in liste:
            a = elem.find_all("a")
            for author in a:
                if re.search("auteurs", author["href"]) != None:
                    authors.append(author.contents[0].strip())
    else:
        auth = soup.find_all("span", {"class" : "author-name"})
        authors = []
        for author in auth:
            author = repr(author.text).replace("\\xa0", " ").replace("\\t", "").replace("\\n", "").replace("'", "")
            if author not in authors:
                authors.append(author)
    if len(authors) > 0:
        mult_items[url]["auteurs"] = authors
    else:
        mult_items[url]["auteurs"] = "NA"
        
    #Liens
    page_links = soup.find_all("h3", {"class" : "h3 uppercase"})
    links = []
    for link in page_links:
        links.append("https://www.millenaire3.com"+link.a["href"])
    if len(links) > 0:
        mult_items[url]["liens"] = links
    else:
        mult_items[url]["liens"] = "NA"
    
    return(mult_items, errors)

In [32]:
def get_article_info(soup, type, url, container, errors):

    #RESUME
    if type == "Dossier":
        resume = soup.find("div", {"class" : "eztext-field"})
    elif type == "Interview":
        resume = soup.find("div", {"class" : "ezrichtext-field"})
    else: 
        resume = soup.find("div", {"class" : "eztext-field"})
    if len(resume) > 0:
        container["RESUME"].append(resume.text)
    else:
        errors["RESUME"].append(url)
        container["RESUME"].append("NA")

    #ARTICLE
    if type != "Interview":
        try:
            article = soup.find("div",  {"class" : "ezrichtext-field"}).text
        except:
            article = ""
    else:
        lines = soup.find_all("div", {"class" : "interview-item"})
        if len(lines) == 0:
            art = soup.find_all("div",  {"class" : "ezrichtext-field"})
            for info in art:
                if info != resume.text:
                    article = info.text
        else:
            article = ""
            for i, line in enumerate(lines):
                article += line.find("p", {"class" : "over-under-line"}).text + " "
                temp = line.find_all("div", {"class" : "ezrichtext-field"})
                for info in temp:
                    article += info.find("p").text
    if len(article) > 0:
        container["ARTICLE"].append(article.replace("\n", " "))
    else:
        errors["ARTICLE"].append(url)
        container["ARTICLE"].append("NA")

    #TITRE
    titre = soup.find("h1", {"class": "uppercase h1-special"}).contents[0]
    titre = titre.replace("\n", "").replace("\t", "").strip()
    if len(titre) > 0:
        container["TITRE"].append(titre)
    else:
        errors["TITRE"].append(url)
        container["TITRE"].append("NA")
        
    #ID - in db
    try:
        ID = soup.find("article", {"class" : "sidebar-block-classic sidebar-block-download"})
        ID = ID.a["href"].split("/")
        ID = ID[len(ID)-1]
        container["IDinDB"].append(ID)
    except:
        container["IDinDB"].append("NA")

    #DATE
    date = soup.find("span", {"class" : "publication_date"}).text
    if len(date) > 0:
        container["DATE"].append(date)
    else:
        errors["DATE"].append(url)
        container["DATE"].append("NA")
    
    #URL
    container["URL"].append(url)
    return(container, errors)

In [37]:
def scrap_page(page, container, mult_items, errors, HTML_FOLDER, url, ONLY_MULT = False):
    
    # html = requests.get(url)
    # if(html.status_code) != 200:
    #     print(html.status_code)
    #     errors["deadlink"].append(url)
    #     return(1)
    # soup = BeautifulSoup(html.text, "html.parser")
    with open(HTML_FOLDER+page, "r", encoding="utf8") as f:
        html= f.read()
    soup = BeautifulSoup(html, "html.parser")
    
    #TYPE
    type_liste = soup.find_all("p", {"class" : re.compile("^over-under")})
    if len(type_liste) > 0:
        type = ""
        for typ in type_liste:
            if re.search("Étude|Dossier|Article|Texte|Interview", typ.text) == None:
                continue
            else:
                if re.search("Interview|Texte", typ.text) == None:
                    type = typ.text.replace("\n", "").replace("\t", "").replace(" ", "")
                elif re.search("Texte", typ.text) != None:
                    type = "Texte"
                    txt_de = typ.text.replace("\n", "").replace("\t", "")
                elif re.search("Interview", typ.text) != None:
                    type = "Interview"
                    itw_de = typ.text.replace("\n", "").replace("\t", "")
    else:
        return(1)
    if len(type) > 0:
        container["TYPE"].append(type)
    else:
        errors["TYPE"].append(url)
        return(1)
    #END TYPE

    if ONLY_MULT == True:
        get_metadata(soup, type, url, mult_items, errors)
    else:
        get_article_info(soup, type, url, container, errors)
        get_metadata(soup, type, url, mult_items, errors)

    return(container, mult_items, errors)


In [39]:
ONLY_MULT = False
HTML_FOLDER = "../urls/"

with open("../data/M3urls3.txt", "r") as f:
        uris = f.read().split("\n")

uris2 = [uri.replace("/", "_").replace(".", "_").replace(":", "_").replace("?", "_").replace("=", "_").replace("&", "_").replace("%", "_").replace("-", "_").replace("httpswwwmillenaire3com", "_").replace("_", "") for uri in uris]

urls = os.listdir(HTML_FOLDER)
#urls.sort(key = lambda x: int(x.replace(".html", "")))

container = {"URL" : [], 
                "TITRE" : [], 
                "IDinDB" : [], 
                "TYPE" : [], 
                "RESUME" : [], 
                "ARTICLE" : [],
                "DATE" : []}

mult_items = {}

errors = {
        "TITRE" : [],
        "TYPE" : [],
        "RESUME" : [],
        "ARTICLE" : [],
        "DATE" : [],
        "deadlink" : []
    }

for i, url in enumerate(urls):
    uri = uris[uris2.index(url.replace(".html", ""))]
    print(f"""\r{i}/{len(urls)} : {url}, {url.replace(".html", "")} : {uri}""", end = "")
    if re.search("/ressources/|/Interviews/|/dossiers/|/actualites-a-la-une/|/publications/", uri) and len(url) > 0:
        scrap_page(url, container, mult_items, errors, HTML_FOLDER, uri, ONLY_MULT)
    else:
        pass
        #print("not an article")


for keys in container:
    print(keys, ":", len(container[keys]))


6144/6145 : httpswwwmillenaire3comuploadstxressm3Vivreetimaginerlaville02pdf.html, httpswwwmillenaire3comuploadstxressm3Vivreetimaginerlaville02pdf : https://www.millenaire3.com/uploads/tx_ressm3/Vivre_et_imaginer_la_ville_02.pdfURL : 3603ion-pour-les-territoires https://www.millenaire3.com/texte-d-auteur/Grandir-en-banlieue-parcours-construction-identitaire-et-positions-sociales.-Le-devenir-d-une-cohortepoleicole-du-departement-du-rhonela-Part-Dieucial-des-doctrines-fondatrices-d-une-tradition-d-anti-individualille-pedagogiet-plus-efficacesham-lyon-et-turinte_debut=01%2F01%2F1900&date_debut_mobile=&date_fin=31%2F12%2F2025&date_fin_mobile=&identifiers=&rubriques=es=es=ulte-a-communiquer-avec-l-administrationes-a-vivre-et-evoluerelopper-autrexpationlitique-elle-con
TITRE : 3603
IDinDB : 3603
TYPE : 3603
RESUME : 3603
ARTICLE : 3603
DATE : 3603


In [41]:
with open("")

{'https://www.millenaire3.com/dossiers/1998/les-cahiers-millenaire-3-archives': {'auteurs': 'NA',
  'tags': ['Prospective'],
  'liens': ['https://www.millenaire3.com/dossiers/1998/les-cahiers-millenaire-3-archives/Cahier-Millenaire-3-n-32-Images-et-signes-Le-trop-plein',
   'https://www.millenaire3.com/dossiers/1998/les-cahiers-millenaire-3-archives/Cahier-Millenaire-3-n-31-Apprendre-et-eduquer',
   'https://www.millenaire3.com/dossiers/1998/les-cahiers-millenaire-3-archives/cahier-millenaire-3-n-30-humanite-en-peril-humanite-en-avenir',
   'https://www.millenaire3.com/dossiers/1998/les-cahiers-millenaire-3-archives/Cahier-Millenaire-3-n-29-Entre-raison-et-deraison-Des-enjeux-de-societe',
   'https://www.millenaire3.com/dossiers/1998/les-cahiers-millenaire-3-archives/Cahier-Millenaire-3-n-28-Lexique',
   'https://www.millenaire3.com/dossiers/1998/les-cahiers-millenaire-3-archives/Cahier-Millenaire-3-n-28-Integration-et-cohesion-en-Europe',
   'https://www.millenaire3.com/dossiers/1998/

In [7]:
for keys in container:
    print(len(container[keys]))

4766
4766
4766
4766
4766
4766
4766


In [44]:
# container["URL"].append("NA")
# container["TITRE"].append("NA")
# container["IDinDB"].append("NA")
# container["ARTICLE"].append("NA")
# container["DATE"].append("NA")
with open(EXPORT_FOLDER+"data_items.json", "w", encoding="utf8") as f:
    f.write(json.dumps(mult_items, indent=4))
tab = pd.DataFrame(container)
tab.to_csv(EXPORT_FOLDER+"data_article.csv")
tab

URL  \
0     https://www.millenaire3.com/dossiers/1998/les-...   
1     https://www.millenaire3.com/dossiers/1998/les-...   
2     https://www.millenaire3.com/dossiers/1998/les-...   
3     https://www.millenaire3.com/dossiers/1998/les-...   
4     https://www.millenaire3.com/dossiers/1998/les-...   
...                                                 ...   
3598  https://www.millenaire3.com/ressources/vivre-e...   
3599  https://www.millenaire3.com/ressources/vous-av...   
3600  https://www.millenaire3.com/ressources/watersc...   
3601  https://www.millenaire3.com/ressources/yves-ch...   
3602  https://www.millenaire3.com/ressources/zoom-su...   

                                                  TITRE  IDinDB     TYPE  \
0                   Les Cahiers Millénaire 3 (archives)      NA  Dossier   
1     Cahier Millénaire 3 n°10 : L'agglomération lyo...  474686    Étude   
2     Cahier Millénaire 3 n°11 : Les loisirs reflets...  474778    Étude   
3     Cahier Millénaire 3 n°12 : Construire le dével...  475168    Étude   
4     Cahier Millénaire 3 n°13 : La santé, enjeux de...  475236    Étude   
...                                                 ...     ...      ...   
3598  Vivre et imaginer la ville : entre cité et mét...      NA  Article   
3599                        Vous avez dit intégration ?   36397    Texte   
3600                 Waterscapes, les paysages de l'eau   24680    Texte   
3601                                       Yves CHAUVIN   14478    Étude   
3602                    Zoom sur l’éducation à la santé   41207    Étude   

                                                 RESUME  \
0     Découvrez la collection des Cahiers Millénaire...   
1     Quatre regards journalistiques, qu’accompagne ...   
2     La diversité des acteurs qui, au sein de l’agg...   
3     Vingt ans après le “rapport Barre“, dix ans ap...   
4     L’étude menée par SANESCO, pour la Communauté ...   
...                                                 ...   
3598                                                 NA   
3599  Jean-Stephan Clerc, témoigne ici de la politiq...   
3600                                                 NA   
3601  Yves Chauvin est né en 1930 à Menin en Belgiqu...   
3602                                                 NA   

                                                ARTICLE        DATE  
0     Les Cahiers Millénaire 3 : ● Cahier Millénaire...  13/02/1998  
1     Sommaire : SportsCulture(s)Citoyenneté, solida...  11/09/1998  
2     Sommaire : 1 - Vers une civilisation des loisi...  11/11/1998  
3     Sommaire : 1. Un contexte nouveau : quelles tr...  16/03/1999  
4     Sommaire : IntroductionLe système de santéLe s...  16/03/1999  
...                                                 ...         ...  
3598  Contexte des synthèsesLa vie sociale contempor...  02/04/2009  
3599  Quelques soient les définitions de l’intégrati...  01/01/2002  
3600  Article écrit pour la revue M3 n°5L’Atelier Dr...  01/06/2013  
3601  Une carrière discrète de chercheur atypique et...  02/01/2007  
3602  L’éducation à la santé joue un rôle décisif da...  25/10/2005  

[3603 rows x 7 columns]

In [39]:
i = 0
for URL in urls:
    if URL not in container["URL"] and URL not in errors["deadlink"] and "partage_email" not in URL and "/auteurs/" not in URL and "/tag/" not in URL:
        i += 1
        print(i, URL)

1 https://www.millenaire3.com
2 https://www.millenaire3.com/
3 https://www.millenaire3.com#content
4 https://www.millenaire3.com#main-menu
5 https://www.millenaire3.com#block-search
6 https://www.millenaire3.com/nos-flux-rss
7 https://www.millenaire3.com/societe
8 https://www.millenaire3.com/modes-d-action
9 https://www.millenaire3.com/transformation-urbaine
10 https://www.millenaire3.com/politiques-publiques
11 https://www.millenaire3.com/territoire
12 https://www.millenaire3.com/soutenabilite
13 https://www.millenaire3.com/actualites-a-la-une/le-rapport-a-la-proprete-urbaine
14 https://www.millenaire3.com/actualites-a-la-une/veille-m3-famille-du-concept-de-fraternite
15 https://www.millenaire3.com/actualites-a-la-une/le-spectacle-vivant-au-defi-de-la-jeunesse-et-du-numerique
16 https://www.millenaire3.com/actualites-a-la-une/crise-ecologique-le-metabolisme-de-l-economie-au-caeur-des-enjeux
17 https://www.millenaire3.com#carousel-example-generic
18 https://www.millenaire3.com#onglet_1

In [40]:
urls[7888]

'https://www.millenaire3.com/dossiers/Les-Cahiers-Millenaire-3-archive/Cahier-Millenaire-3-n-21-Une-agglomeration-competitive-et-rassemblee'

In [9]:
errors

{'TITRE': [],
 'TYPE': ['https://www.millenaire3.com',
  'https://www.millenaire3.com/',
  'https://www.millenaire3.com#content',
  'https://www.millenaire3.com#main-menu',
  'https://www.millenaire3.com#block-search',
  'https://www.millenaire3.com/societe',
  'https://www.millenaire3.com/modes-d-action',
  'https://www.millenaire3.com/transformation-urbaine',
  'https://www.millenaire3.com/politiques-publiques',
  'https://www.millenaire3.com/territoire',
  'https://www.millenaire3.com/soutenabilite',
  'https://www.millenaire3.com/actualites-a-la-une/le-nouveau-conseil-de-developpement-de-la-metropole-s-installe-le-22-juin',
  'https://www.millenaire3.com/actualites-a-la-une/le-dernier-m3-vient-de-sortir',
  'https://www.millenaire3.com/actualites-a-la-une/un-nouveau-millenaire3-flambant-neuf',
  'https://www.millenaire3.com/actualites-a-la-une/place-aux-nudges',
  'https://www.millenaire3.com/actualites-a-la-une/le-second-coworking-tour-dedie-aux-entreprises-a-eu-lieu-!',
  'https: